In [104]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [105]:
path = "/content/drive/MyDrive/homework.zip"

In [106]:
import shutil

In [107]:
shutil.unpack_archive(path, "/content/drive/MyDrive")

In [108]:
mypath = "/content/drive/MyDrive/data"

In [109]:
from os import listdir, path
from os.path import isfile, join
import numpy as np
import pandas as pd

activities = listdir(mypath)
activities

['idle', 'running', 'stairs', 'walking']

In [110]:
for act in activities:
  path = join(mypath, act)
  frames = listdir(path)
  print(act, ':  ', len(frames))

idle :   1039
running :   3408
stairs :   165
walking :   1850


In [111]:
frames = listdir(join(mypath, 'walking'))
frame = pd.read_csv(join(join(mypath, 'walking'),frames[5]))
frame[:5]

accelerometer_X  accelerometer_Y  accelerometer_Z
0        -4.352658        -9.327810         0.713472
1        -3.955221       -16.496050         3.438074
2        -2.705448        -7.436390         1.383849
3        -4.577713       -17.645266         1.944092
4         7.192182       -25.201366       -16.903065

In [113]:
import os
for folder in listdir(mypath):
    folder_path = os.path.join(mypath, folder)
    
    if os.path.isdir(folder_path):
        combined_data = pd.DataFrame() 
        
        for file in os.listdir(folder_path):
            file_path = os.path.join(folder_path, file)
            
            if file.endswith(".csv"):
                data = pd.read_csv(file_path)
                
                combined_data = combined_data.append(data, ignore_index=True)
        
        output_file = os.path.join(mypath, f"{folder}.csv")
        combined_data.to_csv(output_file, index=False)

Выходные данные были обрезаны до нескольких последних строк (5000).
<ipython-input-113-c25070e22e31>:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  combined_data = combined_data.append(data, ignore_index=True)
<ipython-input-113-c25070e22e31>:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  combined_data = combined_data.append(data, ignore_index=True)
<ipython-input-113-c25070e22e31>:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  combined_data = combined_data.append(data, ignore_index=True)
<ipython-input-113-c25070e22e31>:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  combined_data = combined_data.append(data, ignore_index=Tr

In [114]:
listdir(mypath)

['idle',
 'running',
 'stairs',
 'walking',
 'idle.csv',
 'running.csv',
 'stairs.csv',
 'walking.csv']

In [116]:
pd.read_csv(mypath + '/idle.csv')

accelerometer_X  accelerometer_Y  accelerometer_Z
0             1.000776         4.616021         8.576031
1             0.718261         4.209007         8.446744
2            -0.909797        -0.282516         9.203311
3             5.099650         0.148441         8.418014
4             1.762132        -0.162806         9.251195
...                ...              ...              ...
31165         0.344765        -0.009577         9.753978
31166         0.373495         0.009577         9.758766
31167         0.416591        -0.033519         9.753978
31168         0.368707        -0.014365         9.768343
31169         0.378284        -0.023942         9.730036

[31170 rows x 3 columns]

In [123]:
files_css = []
for file in os.listdir(mypath):
  if file.endswith('.csv'):
    files_css.append(join(mypath, file))
files_css

['/content/drive/MyDrive/data/idle.csv',
 '/content/drive/MyDrive/data/running.csv',
 '/content/drive/MyDrive/data/stairs.csv',
 '/content/drive/MyDrive/data/walking.csv']

# Data preparating

In [27]:
from sklearn.metrics import mean_squared_error, mean_absolute_error

from scipy.fftpack import fft, rfft

from sklearn import preprocessing

In [124]:
df_idle = pd.read_csv(files_css[0])

In [135]:
df_idle.head(5)

accelerometer_X  accelerometer_Y  accelerometer_Z
0         1.000776         4.616021         8.576031
1         0.718261         4.209007         8.446744
2        -0.909797        -0.282516         9.203311
3         5.099650         0.148441         8.418014
4         1.762132        -0.162806         9.251195

In [136]:
df_idle.isnull().any().any()

False

In [126]:
df_running = pd.read_csv(files_css[1])

In [127]:
df_running.head(5)

accelerometer_X  accelerometer_Y  accelerometer_Z
0        -4.151545         1.781286         2.173935
1         2.020706         3.706224         9.921572
2         1.762132         4.242526         8.078037
3        -0.445322        11.080365         6.756438
4         5.573702        13.436260        15.054740

In [137]:
df_running.isnull().any().any()

False

In [129]:
df_stairs = pd.read_csv(files_css[2])

In [130]:
df_stairs.head(5)

accelerometer_X  accelerometer_Y  accelerometer_Z
0         6.727707         2.973599         3.936068
1         7.891289         0.440533        -3.342306
2         6.301539        -1.154005         0.067038
3         4.534618        -5.755661        -1.369483
4         4.563349        -3.730166        -0.028730

In [139]:
df_stairs.isnull().any().any()

False

In [131]:
df_walking = pd.read_csv(files_css[3])

In [132]:
df_walking.head(5)

accelerometer_X  accelerometer_Y  accelerometer_Z
0         2.322376         3.643975        11.827356
1         1.781286         4.668694         6.148310
2         7.963115        -4.113238         1.359907
3         1.996764        -1.398214         1.163582
4         5.185841       -12.143391         4.687847

In [138]:
df_walking.isnull().any().any()

False

In [141]:
df_idle_features = pd.DataFrame({
    'mean_X': [df_idle['accelerometer_X'].mean()],
    'mean_Y': [df_idle['accelerometer_Y'].mean()],
    'mean_Z': [df_idle['accelerometer_Z'].mean()],
    'std_X': [df_idle['accelerometer_X'].std()],
    'std_Y': [df_idle['accelerometer_Y'].std()],
    'std_Z': [df_idle['accelerometer_Z'].std()],
    'max_X': [df_idle['accelerometer_X'].max()],
    'max_Y': [df_idle['accelerometer_Y'].max()],
    'max_Z': [df_idle['accelerometer_Z'].max()],
    'min_X': [df_idle['accelerometer_X'].min()],
    'min_Y': [df_idle['accelerometer_Y'].min()],
    'min_Z': [df_idle['accelerometer_Z'].min()],
    'median_X': [df_idle['accelerometer_X'].median()],
    'median_Y': [df_idle['accelerometer_Y'].median()],
    'median_Z': [df_idle['accelerometer_Z'].median()],
    'sum_X': [df_idle['accelerometer_X'].sum()],
    'sum_Y': [df_idle['accelerometer_Y'].sum()],
    'sum_Z': [df_idle['accelerometer_Z'].sum()]
})


In [142]:
df_idle_features

mean_X    mean_Y    mean_Z     std_X     std_Y     std_Z     max_X  \
0  0.096767  2.225971  8.973247  0.691892  2.821235  1.211058  8.135497   

      max_Y      max_Z      min_X     min_Y     min_Z  median_X  median_Y  \
0  9.916783  21.988348 -10.448297 -2.595315 -0.296881  0.234632   0.02873   

   median_Z        sum_X         sum_Y          sum_Z  
0  9.749189  3016.239864  69383.508951  279696.094989

In [143]:
df_running_features = pd.DataFrame({
    'mean_X': [df_running['accelerometer_X'].mean()],
    'mean_Y': [df_running['accelerometer_Y'].mean()],
    'mean_Z': [df_running['accelerometer_Z'].mean()],
    'std_X': [df_running['accelerometer_X'].std()],
    'std_Y': [df_running['accelerometer_Y'].std()],
    'std_Z': [df_running['accelerometer_Z'].std()],
    'max_X': [df_running['accelerometer_X'].max()],
    'max_Y': [df_running['accelerometer_Y'].max()],
    'max_Z': [df_running['accelerometer_Z'].max()],
    'min_X': [df_running['accelerometer_X'].min()],
    'min_Y': [df_running['accelerometer_Y'].min()],
    'min_Z': [df_running['accelerometer_Z'].min()],
    'median_X': [df_running['accelerometer_X'].median()],
    'median_Y': [df_running['accelerometer_Y'].median()],
    'median_Z': [df_running['accelerometer_Z'].median()],
    'sum_X': [df_running['accelerometer_X'].sum()],
    'sum_Y': [df_running['accelerometer_Y'].sum()],
    'sum_Z': [df_running['accelerometer_Z'].sum()]
})

In [144]:
df_running_features

mean_X    mean_Y    mean_Z     std_X      std_Y     std_Z      max_X  \
0  5.045705  8.083135  1.387356  9.952696  12.441402  7.004236  39.188293   

       max_Y      max_Z      min_X      min_Y      min_Z  median_X  median_Y  \
0  39.188293  39.188293 -39.188293 -39.188293 -39.188293  3.605668  7.967903   

   median_Z          sum_X          sum_Y          sum_Z  
0  0.407014  515872.914034  826419.709676  141843.236611

In [145]:
df_stairs_features = pd.DataFrame({
    'mean_X': [df_stairs['accelerometer_X'].mean()],
    'mean_Y': [df_stairs['accelerometer_Y'].mean()],
    'mean_Z': [df_stairs['accelerometer_Z'].mean()],
    'std_X': [df_stairs['accelerometer_X'].std()],
    'std_Y': [df_stairs['accelerometer_Y'].std()],
    'std_Z': [df_stairs['accelerometer_Z'].std()],
    'max_X': [df_stairs['accelerometer_X'].max()],
    'max_Y': [df_stairs['accelerometer_Y'].max()],
    'max_Z': [df_stairs['accelerometer_Z'].max()],
    'min_X': [df_stairs['accelerometer_X'].min()],
    'min_Y': [df_stairs['accelerometer_Y'].min()],
    'min_Z': [df_stairs['accelerometer_Z'].min()],
    'median_X': [df_stairs['accelerometer_X'].median()],
    'median_Y': [df_stairs['accelerometer_Y'].median()],
    'median_Z': [df_stairs['accelerometer_Z'].median()],
    'sum_X': [df_stairs['accelerometer_X'].sum()],
    'sum_Y': [df_stairs['accelerometer_Y'].sum()],
    'sum_Z': [df_stairs['accelerometer_Z'].sum()]
})

In [146]:
df_stairs_features

mean_X    mean_Y    mean_Z     std_X     std_Y     std_Z      max_X  \
0  0.353135 -9.574353 -1.841333  3.845949  4.922294  5.297376  14.164097   

      max_Y      max_Z      min_X      min_Y     min_Z  median_X  median_Y  \
0  4.994305  17.492037 -11.238382 -25.828648 -38.08696  0.483629 -8.944737   

   median_Z        sum_X         sum_Y        sum_Z  
0  -1.58975  1748.016884 -47393.045005 -9114.596029

In [147]:
df_walking_features = pd.DataFrame({
    'mean_X': [df_walking['accelerometer_X'].mean()],
    'mean_Y': [df_walking['accelerometer_Y'].mean()],
    'mean_Z': [df_walking['accelerometer_Z'].mean()],
    'std_X': [df_walking['accelerometer_X'].std()],
    'std_Y': [df_walking['accelerometer_Y'].std()],
    'std_Z': [df_walking['accelerometer_Z'].std()],
    'max_X': [df_walking['accelerometer_X'].max()],
    'max_Y': [df_walking['accelerometer_Y'].max()],
    'max_Z': [df_walking['accelerometer_Z'].max()],
    'min_X': [df_walking['accelerometer_X'].min()],
    'min_Y': [df_walking['accelerometer_Y'].min()],
    'min_Z': [df_walking['accelerometer_Z'].min()],
    'median_X': [df_walking['accelerometer_X'].median()],
    'median_Y': [df_walking['accelerometer_Y'].median()],
    'median_Z': [df_walking['accelerometer_Z'].median()],
    'sum_X': [df_walking['accelerometer_X'].sum()],
    'sum_Y': [df_walking['accelerometer_Y'].sum()],
    'sum_Z': [df_walking['accelerometer_Z'].sum()]
})

In [148]:
df_walking_features

mean_X    mean_Y    mean_Z     std_X     std_Y     std_Z     max_X  \
0 -2.661943 -9.703702 -1.126623  4.648378  5.931165  6.927679  20.57577   

       max_Y      max_Z     min_X      min_Y     min_Z  median_X  median_Y  \
0  14.441825  38.426937 -26.81506 -39.188293 -39.16914 -2.298433 -9.974244   

   median_Z          sum_X          sum_Y         sum_Z  
0 -0.933739 -147737.820092 -538555.441522 -62527.593189

In [149]:
df_features = pd.concat([df_idle_features, df_running_features, df_stairs_features, df_walking_features], axis=0, ignore_index=True)


In [150]:
df_features

mean_X    mean_Y    mean_Z     std_X      std_Y     std_Z      max_X  \
0  0.096767  2.225971  8.973247  0.691892   2.821235  1.211058   8.135497   
1  5.045705  8.083135  1.387356  9.952696  12.441402  7.004236  39.188293   
2  0.353135 -9.574353 -1.841333  3.845949   4.922294  5.297376  14.164097   
3 -2.661943 -9.703702 -1.126623  4.648378   5.931165  6.927679  20.575770   

       max_Y      max_Z      min_X      min_Y      min_Z  median_X  median_Y  \
0   9.916783  21.988348 -10.448297  -2.595315  -0.296881  0.234632  0.028730   
1  39.188293  39.188293 -39.188293 -39.188293 -39.188293  3.605668  7.967903   
2   4.994305  17.492037 -11.238382 -25.828648 -38.086960  0.483629 -8.944737   
3  14.441825  38.426937 -26.815060 -39.188293 -39.169140 -2.298433 -9.974244   

   median_Z          sum_X          sum_Y          sum_Z  
0  9.749189    3016.239864   69383.508951  279696.094989  
1  0.407014  515872.914034  826419.709676  141843.236611  
2 -1.589750    1748.016884  -47393.045005   -9114.596029  
3 -0.933739 -147737.820092 -538555.441522  -62527.593189

In [154]:
from sklearn.model_selection import train_test_split
from sklearn.svm import SVC
from sklearn.ensemble import RandomForestClassifier


labels = ['walking', 'standing', 'running', 'stairs']

X_train, X_test, y_train, y_test = train_test_split(df_features, labels, test_size=0.2, random_state=42)

svm_model = SVC()
rf_model = RandomForestClassifier()

svm_model.fit(X_train, y_train)
rf_model.fit(X_train, y_train)

svm_accuracy = svm_model.score(X_test, y_test)
rf_accuracy = rf_model.score(X_test, y_test)

print("Точність моделі SVM:", svm_accuracy)
print("Точність моделі випадкового лісу:", rf_accuracy)


Точність моделі SVM: 0.0
Точність моделі випадкового лісу: 0.0


# Data preparating

In [155]:
from sklearn.metrics import mean_squared_error, mean_absolute_error

from scipy.fftpack import fft, rfft

from sklearn import preprocessing

### Feature calculation functions

In [156]:
features = [ 
            'skew_X',
            'skew_Y',
            'skew_Z',
            'kurtosis_X',
            'kurtosis_Y',
            'kurtosis_Z',
            'max_X',
            'max_Y',
            'max_Z',
            'min_X',
            'min_Y',
            'min_Z',
            'mean_X',
            'mean_Y',
            'mean_Z',
            'std_X',
            'std_Y',
            'std_Z',
            'variance_X',
            'variance_Y',
            'variance_Z',
            'median_X',
            'median_Y',
            'median_Z',
            'index_max_X',
            'index_max_Y',
            'index_max_Z',
            'index_min_X',
            'index_min_Y',
            'index_min_Z',
            'correlation_X_Y',
            'correlation_X_Z',
            'correlation_Y_Z',
            'mae_X', 'mae_Y','mae_Z', 'rmse_X', 'rmse_Y', 'rmse_Z']

len(features)

39

Create function that will be calculate all statistic features



In [157]:
def get_stat_features(frame):

  features = []
  features = np.array(features)

  features = np.concatenate((features, frame.skew(axis=0).values), axis=0)

  features = np.concatenate((features, frame.kurt(axis=0).values), axis=0)

  features = np.concatenate((features, frame.max(axis=0).values), axis=0)

  features = np.concatenate((features, frame.min(axis=0).values), axis=0)

  features = np.concatenate((features, frame.mean(axis=0).values), axis=0)

  features = np.concatenate((features, frame.std(axis=0).values), axis=0)

  features = np.concatenate((features, frame.var(axis=0).values), axis=0)

  features = np.concatenate((features, frame.median(axis=0).values), axis=0)

  features = np.concatenate((features, frame.idxmax(axis=0).values), axis=0)

  features = np.concatenate((features, frame.idxmin(axis=0).values), axis=0)

  correlations = frame.corr()

  corr = np.array([correlations['accelerometer_X']['accelerometer_Y'], correlations['accelerometer_X']['accelerometer_Z'], correlations['accelerometer_Z']['accelerometer_Y']])

  features = np.concatenate((features, corr), axis=0)

  frame['mean_X'] = frame.mean(axis=0)['accelerometer_X']
  frame['mean_Y'] = frame.mean(axis=0)['accelerometer_Y']
  frame['mean_Z'] = frame.mean(axis=0)['accelerometer_Z']

  mae_X = mean_absolute_error(frame['accelerometer_X'], frame['mean_X'])
  mae_Y = mean_absolute_error(frame['accelerometer_Y'], frame['mean_Y'])
  mae_Z = mean_absolute_error(frame['accelerometer_Z'], frame['mean_Z'])

  rmse_x = np.sqrt(mean_squared_error(frame['accelerometer_X'], frame['mean_X']))
  rmse_y = np.sqrt(mean_squared_error(frame['accelerometer_Y'], frame['mean_Y']))
  rmse_z = np.sqrt(mean_squared_error(frame['accelerometer_Z'], frame['mean_Z']))

  metrics = np.array([mae_X, mae_Y, mae_Z, rmse_x, rmse_y, rmse_z])

  features = np.concatenate((features, metrics), axis=0)

  return features

In [158]:
len(get_stat_features(frame))

39

Create function that will be calculate all Fast Fourier Transform coefficients

In [159]:
def get_fft_features(frame):

  fft_X = np.array(preprocessing.normalize([rfft(frame['accelerometer_X'].values)])[0])
  fft_Y = np.array(preprocessing.normalize([rfft(frame['accelerometer_Y'].values)])[0])
  fft_Z = np.array(preprocessing.normalize([rfft(frame['accelerometer_Z'].values)])[0])

  features = np.concatenate((fft_X, fft_Y), axis=0)
  features = np.concatenate((features, fft_Z), axis=0)

  return features

### Discover calculation of features

In [160]:
a = np.array([2])

In [161]:
frame.skew(axis=0).values

a = np.concatenate((a, frame.skew(axis=0).values), axis=0)

a

array([ 2.        , -0.32384742,  0.16223744,  2.06164601,  0.        ,
        0.        ,  0.        ])

In [162]:
frame.kurt(axis=0)

accelerometer_X     0.134180
accelerometer_Y     0.542627
accelerometer_Z    10.326116
mean_X              0.000000
mean_Y              0.000000
mean_Z              0.000000
dtype: float64

In [163]:
frame.max(axis=0)

accelerometer_X    11.113884
accelerometer_Y     6.435614
accelerometer_Z    32.599450
mean_X              0.285548
mean_Y            -10.916123
mean_Z              0.366473
dtype: float64

In [164]:
frame.min(axis=0)

accelerometer_X   -12.277467
accelerometer_Y   -25.201366
accelerometer_Z   -16.903065
mean_X              0.285548
mean_Y            -10.916123
mean_Z              0.366473
dtype: float64

In [165]:
frame.mean(axis=0)

accelerometer_X     0.285548
accelerometer_Y   -10.916123
accelerometer_Z     0.366473
mean_X              0.285548
mean_Y            -10.916123
mean_Z              0.366473
dtype: float64

In [166]:
frame.std(axis=0)

accelerometer_X    5.090906e+00
accelerometer_Y    6.820465e+00
accelerometer_Z    7.811986e+00
mean_X             5.646013e-17
mean_Y             3.613448e-15
mean_Z             1.129203e-16
dtype: float64

In [167]:
frame.var(axis=0)

accelerometer_X    2.591732e+01
accelerometer_Y    4.651874e+01
accelerometer_Z    6.102712e+01
mean_X             3.187746e-33
mean_Y             1.305701e-29
mean_Z             1.275098e-32
dtype: float64

In [168]:
frame.idxmax(axis=0)

accelerometer_X    18
accelerometer_Y    25
accelerometer_Z    11
mean_X              0
mean_Y              0
mean_Z              0
dtype: int64

In [169]:
frame.idxmin(axis=0)

accelerometer_X    25
accelerometer_Y     4
accelerometer_Z     4
mean_X              0
mean_Y              0
mean_Z              0
dtype: int64

In [170]:
frame.corr()['accelerometer_X']['accelerometer_Y']

-0.3445943692306763

In [171]:
frame.median(axis=0)

accelerometer_X     0.773328
accelerometer_Y   -10.345346
accelerometer_Z     0.768539
mean_X              0.285548
mean_Y            -10.916123
mean_Z              0.366473
dtype: float64

In [172]:
from sklearn.metrics import mean_squared_error, mean_absolute_error

In [173]:
new_frame = frame

In [174]:
new_frame['mean_X'] = frame.mean(axis=0)['accelerometer_X']
new_frame['mean_Y'] = frame.mean(axis=0)['accelerometer_Y']
new_frame['mean_Z'] = frame.mean(axis=0)['accelerometer_Z']

new_frame

accelerometer_X  accelerometer_Y  accelerometer_Z    mean_X     mean_Y  \
0         -4.352658        -9.327810         0.713472  0.285548 -10.916123   
1         -3.955221       -16.496050         3.438074  0.285548 -10.916123   
2         -2.705448        -7.436390         1.383849  0.285548 -10.916123   
3         -4.577713       -17.645266         1.944092  0.285548 -10.916123   
4          7.192182       -25.201366       -16.903065  0.285548 -10.916123   
5          1.575385       -10.620679         1.589750  0.285548 -10.916123   
6         -0.028730        -5.425261         0.823605  0.285548 -10.916123   
7          3.418920        -6.675034         1.158794  0.285548 -10.916123   
8          1.891419       -11.669339        -1.570596  0.285548 -10.916123   
9         -1.647211        -5.305551         9.169792  0.285548 -10.916123   
10         3.399767       -15.586253        -0.804452  0.285548 -10.916123   
11         4.572925         0.181959        32.599450  0.285548 -10.916123   
12         5.607220       -13.005303        -0.378284  0.285548 -10.916123   
13         3.672706       -10.874464        -7.058106  0.285548 -10.916123   
14         1.939303        -9.097966        -2.782062  0.285548 -10.916123   
15        -0.344765        -4.161122         1.230620  0.285548 -10.916123   
16        -0.387861        -9.174581         3.031059  0.285548 -10.916123   
17        -7.359776       -15.322891         0.852336  0.285548 -10.916123   
18        11.113884       -19.603724        -3.921702  0.285548 -10.916123   
19         5.109226       -15.452178        -1.470040  0.285548 -10.916123   
20         6.373365       -11.741165        -8.226476  0.285548 -10.916123   
21         3.289633        -9.993398        -0.383072  0.285548 -10.916123   
22        -2.978387        -3.050213         1.273715  0.285548 -10.916123   
23        -4.347870        -9.926360        -1.642422  0.285548 -10.916123   
24        -4.256891       -17.166426        -2.054225  0.285548 -10.916123   
25       -12.277467         6.435614         2.853889  0.285548 -10.916123   
26        -7.886500       -16.826450         4.912902  0.285548 -10.916123   
27         4.137180       -23.673866       -10.807426  0.285548 -10.916123   
28         2.523489       -10.070012         0.158017  0.285548 -10.916123   
29        -0.143652        -3.572149         1.862689  0.285548 -10.916123   

      mean_Z  
0   0.366473  
1   0.366473  
2   0.366473  
3   0.366473  
4   0.366473  
5   0.366473  
6   0.366473  
7   0.366473  
8   0.366473  
9   0.366473  
10  0.366473  
11  0.366473  
12  0.366473  
13  0.366473  
14  0.366473  
15  0.366473  
16  0.366473  
17  0.366473  
18  0.366473  
19  0.366473  
20  0.366473  
21  0.366473  
22  0.366473  
23  0.366473  
24  0.366473  
25  0.366473  
26  0.366473  
27  0.366473  
28  0.366473  
29  0.366473

In [175]:
mean_absolute_error(frame['accelerometer_X'], new_frame['mean_X'])

4.1022251333333335

In [176]:
np.sqrt(mean_squared_error(frame['accelerometer_X'], new_frame['mean_X']))

5.00533805343232

In [177]:
from scipy.fftpack import fft, rfft

In [178]:
frame

accelerometer_X  accelerometer_Y  accelerometer_Z    mean_X     mean_Y  \
0         -4.352658        -9.327810         0.713472  0.285548 -10.916123   
1         -3.955221       -16.496050         3.438074  0.285548 -10.916123   
2         -2.705448        -7.436390         1.383849  0.285548 -10.916123   
3         -4.577713       -17.645266         1.944092  0.285548 -10.916123   
4          7.192182       -25.201366       -16.903065  0.285548 -10.916123   
5          1.575385       -10.620679         1.589750  0.285548 -10.916123   
6         -0.028730        -5.425261         0.823605  0.285548 -10.916123   
7          3.418920        -6.675034         1.158794  0.285548 -10.916123   
8          1.891419       -11.669339        -1.570596  0.285548 -10.916123   
9         -1.647211        -5.305551         9.169792  0.285548 -10.916123   
10         3.399767       -15.586253        -0.804452  0.285548 -10.916123   
11         4.572925         0.181959        32.599450  0.285548 -10.916123   
12         5.607220       -13.005303        -0.378284  0.285548 -10.916123   
13         3.672706       -10.874464        -7.058106  0.285548 -10.916123   
14         1.939303        -9.097966        -2.782062  0.285548 -10.916123   
15        -0.344765        -4.161122         1.230620  0.285548 -10.916123   
16        -0.387861        -9.174581         3.031059  0.285548 -10.916123   
17        -7.359776       -15.322891         0.852336  0.285548 -10.916123   
18        11.113884       -19.603724        -3.921702  0.285548 -10.916123   
19         5.109226       -15.452178        -1.470040  0.285548 -10.916123   
20         6.373365       -11.741165        -8.226476  0.285548 -10.916123   
21         3.289633        -9.993398        -0.383072  0.285548 -10.916123   
22        -2.978387        -3.050213         1.273715  0.285548 -10.916123   
23        -4.347870        -9.926360        -1.642422  0.285548 -10.916123   
24        -4.256891       -17.166426        -2.054225  0.285548 -10.916123   
25       -12.277467         6.435614         2.853889  0.285548 -10.916123   
26        -7.886500       -16.826450         4.912902  0.285548 -10.916123   
27         4.137180       -23.673866       -10.807426  0.285548 -10.916123   
28         2.523489       -10.070012         0.158017  0.285548 -10.916123   
29        -0.143652        -3.572149         1.862689  0.285548 -10.916123   

      mean_Z  
0   0.366473  
1   0.366473  
2   0.366473  
3   0.366473  
4   0.366473  
5   0.366473  
6   0.366473  
7   0.366473  
8   0.366473  
9   0.366473  
10  0.366473  
11  0.366473  
12  0.366473  
13  0.366473  
14  0.366473  
15  0.366473  
16  0.366473  
17  0.366473  
18  0.366473  
19  0.366473  
20  0.366473  
21  0.366473  
22  0.366473  
23  0.366473  
24  0.366473  
25  0.366473  
26  0.366473  
27  0.366473  
28  0.366473  
29  0.366473

In [179]:
frame['accelerometer_X'].values

array([ -4.352658,  -3.955221,  -2.705448,  -4.577713,   7.192182,
         1.575385,  -0.02873 ,   3.41892 ,   1.891419,  -1.647211,
         3.399767,   4.572925,   5.60722 ,   3.672706,   1.939303,
        -0.344765,  -0.387861,  -7.359776,  11.113884,   5.109226,
         6.373365,   3.289633,  -2.978387,  -4.34787 ,  -4.256891,
       -12.277467,  -7.8865  ,   4.13718 ,   2.523489,  -0.143652])

In [180]:
from sklearn import preprocessing

preprocessing.normalize([rfft(frame['accelerometer_X'].values)])[0]

array([ 0.07921776, -0.36261872, -0.23872122, -0.00875992, -0.17069203,
        0.29059423,  0.11034306, -0.27884912,  0.4654557 , -0.02147603,
        0.06779929, -0.11895174,  0.1659198 , -0.16414777, -0.06431846,
        0.12806833, -0.12678634, -0.03159774, -0.23551801,  0.08439857,
       -0.09456619, -0.15296785,  0.25380562, -0.05073099, -0.02089613,
        0.04253843,  0.18901115, -0.1205775 , -0.00540667,  0.24340973])

### Prepare one class (calculation features)

In [181]:
def class_data_prepare(class_name, class_number):

  path = join(mypath, class_name)

  X = []

  for item in listdir(path):
    frame = pd.read_csv(join(path, item))
    frame = frame.values
    frame = frame.flatten()
    X.append(frame)

  y = [class_number]*len(X)

  X = np.array(X)
  y = np.array(y)

  return X, y

In [182]:
def class_data_stat_fft_prepare(class_name, class_number):

  path = join(mypath, class_name)

  X = []

  for item in listdir(path):
    frame = pd.read_csv(join(path, item))
    features_stat = get_stat_features(frame)
    features_fft = get_fft_features(frame)
    features = np.concatenate((features_stat, features_fft), axis=0)
    X.append(features)

  y = [class_number]*len(X)

  X = np.array(X)
  y = np.array(y)

  return X, y

In [183]:
def class_data_fft_prepare(class_name, class_number):

  path = join(mypath, class_name)

  X = []

  for item in listdir(path):
    frame = pd.read_csv(join(path, item))
    features = get_fft_features(frame)
    X.append(features)

  y = [class_number]*len(X)

  X = np.array(X)
  y = np.array(y)

  return X, y

In [184]:
def class_data_stat_prepare(class_name, class_number):

  path = join(mypath, class_name)

  X = []

  for item in listdir(path):
    frame = pd.read_csv(join(path, item))
    features = get_stat_features(frame)
    X.append(features)

  y = [class_number]*len(X)

  X = np.array(X)
  y = np.array(y)

  return X, y

### Create DataSet

In [185]:
def create_dataset(class_prepare):

  X_idle, y_idle = class_prepare('idle', 0)
  X_walking, y_walking = class_prepare('walking', 1)
  X_stairs, y_stairs = class_prepare('stairs', 2)
  X_running, y_running = class_prepare('running', 3)

  X = np.concatenate((X_idle, X_walking), axis=0)
  X = np.concatenate((X, X_stairs), axis=0)
  X = np.concatenate((X, X_running), axis=0)

  Y = np.concatenate((y_idle, y_walking))
  Y = np.concatenate((Y, y_stairs))
  Y = np.concatenate((Y, y_running))

  return X, Y

In [186]:
X_fft, Y_fft = create_dataset(class_data_fft_prepare)

In [187]:
import pickle

In [188]:
with open('fft_data_X.pickle', 'wb') as f:
  pickle.dump(X_fft, f)

with open('fft_data_Y.pickle', 'wb') as f:
  pickle.dump(Y_fft, f)

In [189]:
X_fft_stat, Y_fft_stat = create_dataset(class_data_stat_fft_prepare)

with open('fft_stat_data_X.pickle', 'wb') as f:
  pickle.dump(X_fft_stat, f)

with open('fft_stat_data_Y.pickle', 'wb') as f:
  pickle.dump(Y_fft_stat, f)

In [190]:
from sklearn import model_selection
X_train, X_test, y_train, y_test = model_selection.train_test_split(X_fft_stat, Y_fft_stat, test_size=0.3)

# Old Data preparation

### Idle

In [191]:
idle_path = '/content/drive/MyDrive/data/idle'

idle = []

for item in listdir(idle_path):
  frame = pd.read_csv(join(idle_path, item))
  example = frame.values
  example = example.flatten()
  idle.append(example)

idle

[array([ 1.000776,  4.616021,  8.576031,  0.718261,  4.209007,  8.446744,
        -0.909797, -0.282516,  9.203311,  5.09965 ,  0.148441,  8.418014,
         1.762132, -0.162806,  9.251195, -0.086191, -0.148441,  9.787497,
        -0.062249, -0.191536,  9.773131, -0.057461, -0.114922,  9.763555,
        -0.124498, -0.162806,  9.782708, -0.138864, -0.124498,  9.768343,
        -0.095768, -0.129287,  9.773131, -0.114922, -0.134075,  9.782708,
        -0.114922, -0.134075,  9.744401, -0.09098 , -0.143652,  9.773131,
        -0.095768, -0.129287,  9.782708, -0.105345, -0.114922,  9.763555,
        -0.148441, -0.148441,  9.787497, -0.134075, -0.105345,  9.773131,
        -0.100556, -0.124498,  9.763555, -0.081403, -0.110133,  9.744401,
        -0.124498, -0.153229,  9.773131, -0.320823, -0.191536,  9.792285,
         0.148441, -0.234632,  9.768343,  0.407014,  0.023942,  9.80665 ,
        -0.311246, -0.167594,  9.768343, -0.038307, -0.244209,  9.782708,
        -0.114922, -0.158017,  9.80186

In [192]:
y_idle = [0]*len(idle)
y_idle

[0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,


In [193]:
len(idle)

1039

### Stairs

In [225]:
stairs_path = '/content/drive/MyDrive/data/stairs'

stairs = []

for item in listdir(stairs_path):
  frame = pd.read_csv(join(stairs_path, item))
  example = frame.values
  example = example.flatten()
  stairs.append(example)

stairs

[array([  6.727707,   2.973599,   3.936068,   7.891289,   0.440533,
         -3.342306,   6.301539,  -1.154005,   0.067038,   4.534618,
         -5.755661,  -1.369483,   4.563349,  -3.730166,  -0.02873 ,
         -0.972046,  -6.660669,  -2.954445,  -2.868254,  -5.497087,
          0.23942 ,   2.767697,  -4.932055,   0.110133,   2.470816,
         -7.718906,   2.949657,   4.941633,  -6.833051,  -1.699883,
          1.168371,  -9.816227,   1.910573,   8.073248,  -5.856217,
         -1.359906,   3.366248, -16.82645 ,   1.168371,   7.015011,
        -16.845604,  -7.517793,   4.697424,  -9.074024,  -0.866701,
         -1.546654,  -1.508347,   0.3304  ,   3.830723, -12.014104,
         -1.158794,   2.418144,  -9.002198,   0.823605,   3.529053,
         -7.43639 ,   1.905785,   0.986411, -17.3005  ,  -0.383072,
         -4.582502,  -7.862558,   9.792285,   1.910573,  -5.985504,
         -1.599327,   4.458004,  -6.914454,  -5.401319,   2.475605,
         -8.705317,  -0.373495,  -1.120486,  -5.

In [195]:
y_stairs = [1]*len(stairs)
y_stairs

[1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1]

### Walking

In [196]:
walking_path = '/content/drive/MyDrive/data/walking'

walking = []

for item in listdir(walking_path):
  frame = pd.read_csv(join(walking_path, item))
  example = frame.values
  example = example.flatten()
  walking.append(example)

walking

[array([  2.322376,   3.643975,  11.827356,   1.781286,   4.668694,
          6.14831 ,   7.963115,  -4.113238,   1.359907,   1.996764,
         -1.398214,   1.163582,   5.185841, -12.143391,   4.687847,
         11.219229, -10.625467,  -8.087613,  10.888829, -13.939042,
         -1.273715,   9.902418,  -9.667787,  -0.110133,   8.09719 ,
        -20.9349  ,   1.393425,   5.655105, -11.573571,  -1.106121,
         12.363658, -18.253393, -21.44247 ,   5.171476,  -9.169792,
          0.407014,  -1.92015 ,  -3.648763,   0.244209,   0.11971 ,
         -7.819463,   0.234632,   4.908114, -11.271901,  -2.561796,
          0.363919, -15.289372,  -1.977611,   5.075708, -10.682928,
         -1.565808,  -2.097321, -13.431472,   4.252103,   4.563349,
        -10.31901 ,   0.45011 ,   0.837971,  -5.544971,  -1.441309,
          2.537854,  -8.408437,   0.277727,   2.494758,  -5.980716,
          2.312799,  -2.351106, -14.432248,  -0.972046,   6.540959,
        -10.903194,  -2.03986 ,   5.214572, -10.

In [197]:
y_walking = [2]*len(walking)
y_walking

[2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,


### Running

In [198]:
running_path = '/content/drive/MyDrive/data/running'

running = []

for item in listdir(running_path):
  frame = pd.read_csv(join(running_path, item))
  example = frame.values
  example = example.flatten()
  running.append(example)

running

[array([-4.1515450e+00,  1.7812860e+00,  2.1739350e+00,  2.0207060e+00,
         3.7062240e+00,  9.9215720e+00,  1.7621320e+00,  4.2425260e+00,
         8.0780370e+00, -4.4532200e-01,  1.1080365e+01,  6.7564380e+00,
         5.5737020e+00,  1.3436260e+01,  1.5054740e+01,  1.7812860e+00,
         3.8546650e+00,  7.6853880e+00, -4.9416320e+00,  3.6774940e+00,
         4.3766010e+00,  6.4164610e+00, -3.1795000e+00, -2.1978770e+00,
         1.8780119e+01,  1.9091364e+01,  2.5775976e+01,  4.0078940e+00,
         1.3273455e+01,  5.6838350e+00,  4.7880000e-03, -8.9255840e+00,
        -4.1994300e+00,  9.5528650e+00,  6.1961940e+00,  1.5389929e+01,
         2.8538890e+00,  8.1977470e+00,  1.1425131e+01,  3.3949780e+00,
        -9.3756940e+00, -2.8921960e+00,  7.1969710e+00,  9.8784760e+00,
         7.1826100e-01,  1.8904617e+01,  1.5370775e+01,  1.6184803e+01,
         2.9783870e+00, -9.4810400e-01,  2.2218190e+00,  4.3095600e-01,
         8.8729110e+00,  2.4756050e+00,  1.3924677e+01,  6.22492

In [199]:
y_running = [3]*len(running)
y_running

[3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,
 3,


In [200]:
len(walking)

1850

In [205]:
walking[50]

array([-10.46745 , -15.68681 , -15.251065,  -3.624821,  -7.158663,
        -0.02873 ,  -2.331952,  -3.232172,   1.766921,  -6.29675 ,
        -7.594407,   1.302446,  -9.433155, -13.369223,   0.924162,
        10.457873,  13.895947,  27.241226,  -2.916138, -12.330139,
        -1.173159,  -4.802768,  -9.979033,  -9.634268,  -0.143652,
       -13.512875,  -0.732626,  -3.323152,  -6.933608,  -8.307879,
        -0.924162,  -8.820239,   1.058237,   1.292869,  -8.207323,
         1.192313,   2.063802, -15.040375,  -2.868254,  -8.724471,
       -11.195287,   0.593762,  -5.449203, -11.918336,  -8.078036,
         0.42138 , -12.196063,  -3.825934,   0.588974,  -5.707777,
        -5.78918 ,  -1.244985, -11.295844,  -1.675941,  -3.466804,
        -2.293645,   2.375048,  -4.726154,  -7.982268,  -1.47004 ,
        -6.579266, -12.334928,  -1.843535,  -5.161899,  -3.586514,
        -3.337517,  -3.337517, -13.177686,  -3.763685, -14.839262,
       -16.587029, -20.84871 ,  -5.717354, -12.856863,  -0.732

In [206]:
ex = pd.read_csv(mypath +'/walking/walking-1053.csv')
ex_X = ex.values
ex_X = ex_X.flatten()

In [207]:
stairs = listdir(mypath+'/stairs')

In [208]:
len(stairs)

165

In [224]:
ex = pd.read_csv(mypath+'/stairs/stairs-109.csv')
ex

accelerometer_X  accelerometer_Y  accelerometer_Z
0          0.823605        -7.383718        -3.596091
1         -6.224924       -12.234370       -26.230873
2          1.273715        -6.502651        -3.572149
3          0.723049        -6.871359        -4.079719
4          2.226608        -7.575254       -12.555194
5          3.284845       -11.966220        -3.892972
6          3.945645       -11.760319        -8.097190
7          2.801216        -9.327810        -5.133168
8         -1.350330        -3.380613        -0.057461
9         -0.253785        -6.373365         0.205901
10        -1.608903        -6.502651        -3.998317
11         1.685518       -10.146626        -1.115698
12        -0.474052        -4.137180        -1.249773
13        -0.761356        -9.203311        -2.178723
14        -1.278504        -4.141969         0.253785
15        -0.330400        -6.105214        -3.284845
16         1.455675        -7.479486        -3.864241
17         1.613692        -9.150639        -4.151545
18         1.216255        -9.792285         0.636858
19        -2.547430        -7.086837        -2.585738
20        -1.206678        -9.433155        -2.202665
21        -3.102885        -4.644751        -2.456451
22         0.282516        -9.251195        -0.933739
23        -3.208230        -4.711789         0.885855
24         2.418144        -8.571242        -1.675941
25        -5.861006        -6.397307        -3.375824
26         2.959233        -6.081272        -3.136404
27        -7.805097        -8.365341        -2.130839
28        -0.842759        -6.119579        -1.618480
29        -1.814805        -7.259219        -1.043872

In [210]:
running = listdir(mypath+'/running')
len(running)

3408

In [211]:
ex = pd.read_csv(mypath+'/running/running-1005.csv')
ex

accelerometer_X  accelerometer_Y  accelerometer_Z
0         -5.683835         5.559336         0.067038
1         10.596737        25.924416         4.884172
2          6.335058        -7.580042         4.477157
3         -4.548983         7.465121         2.619257
4         22.261288        11.429919         6.133945
5          5.688624        12.215217        10.749966
6         -6.976703         5.310340        -2.011129
7          7.891289       -14.877569         5.482722
8          9.993398        16.050728        -0.258574
9         -4.165911         6.770803        -4.908113
10        -1.723825        -5.334281        -2.954445
11        18.722658        31.924286         5.631162
12        -8.547300         6.507440        -0.579397
13         8.384495       -11.999739        -2.777274
14         3.155558        10.989386         0.794875
15         3.825935        -0.023942        35.989640
16         2.839523         3.658340        11.942278
17        -4.544194         6.612785         1.254562
18         2.786851        18.918982         5.415684
19         3.208230        -6.708553        -1.608903
20        -4.419696         4.750097         4.209007
21        28.629864        26.125528         1.331176
22         3.284845        -0.162806        -4.486734
23        -2.748543         5.683835        -1.168370
24         0.617704        -8.178592        -4.668693
25        16.864758        27.710491         7.958327
26         2.920926        14.465767         3.040636
27         8.916007        14.834474       -18.957289
28        23.530214        11.463438        -3.648763
29         2.542642        11.190498         2.853889

### Create DataSet

In [239]:
idle.shape

(1039, 90)

In [240]:
stairs = np.array(stairs)
stairs.shape

(165, 90)

In [241]:
import numpy as np

idle = np.array(idle)
stairs = np.array(stairs)

y_idle = np.array(y_idle)
y_stairs = np.array(y_stairs)

X = np.concatenate((idle, stairs), axis=0)
Y = np.concatenate((y_idle, y_stairs))

In [242]:
from sklearn import model_selection
X_train, X_test, y_train, y_test = model_selection.train_test_split(X, Y, test_size=0.3)

In [243]:
Y.shape

(1204,)

In [244]:
X.shape

(1204, 90)

### metrics

In [245]:
def class_counting(y):

  count_idle = 0
  count_walking = 0
  count_stairs = 0
  count_running = 0

  for i in y:
    if i==0 :
      count_idle += 1
    elif i==1 :
      count_walking += 1
    elif i==2 :
      count_stairs += 1
    else:
      count_running += 1

  return count_idle, count_walking, count_stairs, count_running

def make_report(y_pred, y_test):

  idle_pred, walking_pred, stairs_pred, running_pred = class_counting(y_pred)
  idle_test, walking_test, stairs_test, running_test = class_counting(y_test)

  print('idle test -- ', idle_test, 'idle pred -- ', idle_pred)
  print('walking test -- ', walking_test, 'walking pred -- ', walking_pred)
  print('stairs test -- ',  stairs_test, 'stairs_pred -- ', stairs_pred)
  print('running test -- ', running_test, 'running pred -- ', running_pred) 

# Load DataSet

In [246]:
import pickle

def open_data_set(flag):

  name = flag + '_data_'

  with open(name + 'X.pickle', 'rb') as f:
    X = pickle.load(f)

  with open(name + 'Y.pickle', 'rb') as f:
    Y = pickle.load(f)

  return X, Y

You can load DataSet from сorresponding pickle apply this function uses flags 

```
'fft'
'stat'
'fft_stat'
```

for Fast Fourier Transform features, Statistical features and last flag for both


In [247]:
X, Y = open_data_set('fft')

In [248]:
from sklearn import model_selection
X_train, X_test, y_train, y_test = model_selection.train_test_split(X, Y, test_size=0.3)

Checking correct working of loading pickle

In [249]:
np.array_equal(X, X_fft_stat)

False

# SVM Classifier

In [250]:
from sklearn import svm

classifier = svm.SVC(decision_function_shape='ovo', kernel='rbf', gamma=0.005, probability=True)

In [251]:
classifier.fit(X_train, y_train)

SVC(decision_function_shape='ovo', gamma=0.005, probability=True)

In [252]:
y_test

array([3, 3, 3, ..., 1, 3, 3])

In [253]:
y_test_pred = classifier.decision_function(X_test)

y_test_pred

array([[ 0.27283843,  0.12571027, -1.72418885,  1.08251959, -1.18812522,
        -1.22686371],
       [-0.16528717,  0.12306013, -0.66373748,  1.13220022, -1.09426792,
        -1.17563814],
       [-0.22434375, -0.11223587, -1.22787537,  1.08084533, -1.17436492,
        -1.19758362],
       ...,
       [-1.50541487, -0.45126311, -0.27855928,  1.05602135,  1.17295488,
         0.88635232],
       [ 0.05875076,  0.27073889, -0.42179225,  1.14738757, -1.08783212,
        -1.18304501],
       [-0.33276281, -0.08366347, -1.09531978,  1.11772272, -1.21856292,
        -1.24855567]])

In [254]:
y_test_proba = classifier.predict_proba(X_test)

y_test_proba

array([[2.90719904e-07, 1.69765400e-07, 1.53629113e-07, 9.99999386e-01],
       [1.07723118e-02, 2.88449065e-03, 1.45633663e-03, 9.84886861e-01],
       [2.60501000e-07, 4.12392625e-07, 2.12426909e-07, 9.99999115e-01],
       ...,
       [3.77057090e-06, 9.97354253e-01, 2.40836268e-03, 2.33613406e-04],
       [1.43086778e-01, 1.75243980e-02, 1.24252826e-02, 8.26963541e-01],
       [1.77893498e-07, 3.05233893e-07, 1.57483448e-07, 9.99999359e-01]])

In [255]:
y_test_proba = np.argmax(y_test_proba, axis=1)

y_test_proba

array([3, 3, 3, ..., 1, 3, 3])

In [256]:
count_idle = 0
count_walking = 0
count_stairs = 0
count_running = 0

for i in y_test_proba:
  if i==0 :
    count_idle += 1
  elif i==1 :
    count_walking += 1
  elif i==2 :
    count_stairs += 1
  else:
    count_running += 1 

In [257]:
count_idle

316

In [258]:
count_walking

588

In [259]:
count_stairs

33

In [260]:
count_running

1002

In [261]:
from sklearn.metrics import accuracy_score

accuracy = accuracy_score(y_test, y_test_proba)

accuracy

0.9726663228468283

# SVM Classifier on stat features

In [262]:
from sklearn.model_selection import cross_val_score
from sklearn.metrics import f1_score, accuracy_score
from sklearn import svm

In [263]:
classifier = svm.SVC(decision_function_shape='ovo', kernel='rbf', gamma=0.01, probability=True)

In [266]:
classifier.fit(X_train, y_train)

SVC(decision_function_shape='ovo', gamma=0.01, probability=True)

In [267]:
scores = cross_val_score(classifier, X_train, y_train, cv=10)
scores.mean()

0.9741331145363261

In [268]:
y_test_proba = classifier.predict_proba(X_test)

y_test_proba = np.argmax(y_test_proba, axis=1)

accuracy = accuracy_score(y_test, y_test_proba)

accuracy

0.9757607013924704

### With scale gamma

In [269]:
classifier = svm.SVC(decision_function_shape='ovo', probability=True)

In [270]:
classifier.fit(X_train, y_train)

SVC(decision_function_shape='ovo', probability=True)

In [271]:
scores = cross_val_score(classifier, X_train, y_train, cv=10)
scores.mean()

0.9814291156303113

In [ ]:
y_test_proba = classifier.predict_proba(X_test)

y_test_proba = np.argmax(y_test_proba, axis=1)

accuracy = accuracy_score(y_test, y_test_proba)

accuracy

0.9845281072717896

In [272]:
make_report(y_test_proba, y_test)

idle test --  316 idle pred --  318
walking test --  561 walking pred --  588
stairs test --  60 stairs_pred --  33
running test --  1002 running pred --  1000


### With linear kernel

In [273]:
classifier = svm.SVC(decision_function_shape='ovo', probability=True, kernel='linear')

In [274]:
classifier.fit(X_train, y_train)

SVC(decision_function_shape='ovo', kernel='linear', probability=True)

In [275]:
scores = cross_val_score(classifier, X_train, y_train, cv=10)
scores.mean()

0.9778907577799918

In [276]:
y_test_proba = classifier.predict_proba(X_test)

y_test_proba = np.argmax(y_test_proba, axis=1)

accuracy = accuracy_score(y_test, y_test_proba)

accuracy

0.9747292418772563

In [277]:
make_report(y_test_proba, y_test)

idle test --  316 idle pred --  317
walking test --  561 walking pred --  593
stairs test --  60 stairs_pred --  28
running test --  1002 running pred --  1001


In [278]:
classifier.coef_.mean(axis=0)

array([-3.41169647e-01, -6.18732643e-04, -2.56011261e-02,  7.58920521e-03,
       -1.18959493e-01, -3.74407645e-02, -4.40191064e-02, -4.15150532e-02,
        6.94058507e-02, -4.52748631e-04, -8.78383342e-03, -1.53266822e-02,
       -2.41868201e-02, -1.41313184e-03,  1.12678911e-02, -5.93257206e-02,
        3.62757260e-02, -2.26372434e-02,  1.44795364e-02, -5.65959963e-02,
       -1.28980150e-02, -1.48353707e-02,  2.67192881e-02,  5.37972308e-03,
       -5.45519198e-02, -6.75111165e-02,  7.14673266e-04,  5.87734297e-02,
       -9.72618259e-02, -2.20661279e-01, -2.27960465e-02,  1.67056176e-02,
       -4.05331104e-02, -8.56426278e-02, -1.30903664e-01, -4.04789564e-02,
        1.40511573e-01, -7.47463423e-02,  1.46885310e-02, -2.92421587e-02,
       -4.88264990e-03, -1.55893795e-02, -9.78925734e-02, -1.30083193e-02,
        9.39126087e-02, -6.44222944e-02,  5.02946430e-03, -1.30032441e-01,
        7.72418041e-02,  1.59820786e-02,  1.57821652e-01,  3.15201149e-02,
       -4.21055595e-02, -

### SVM OVR with Linear Kernel

# SVM on FFT Data

In [287]:
from sklearn.model_selection import cross_val_score
from sklearn.metrics import f1_score, accuracy_score
from sklearn import svm

In [288]:
classifier = svm.SVC(decision_function_shape='ovo', kernel='rbf', gamma=0.05, probability=True)

scores = cross_val_score(classifier, X_train, y_train, cv=10)
scores.mean()

0.9750175819023618

In [289]:
classifier.fit(X_train, y_train)

y_test_proba = classifier.predict_proba(X_test)

y_test_proba = np.argmax(y_test_proba, axis=1)

accuracy = accuracy_score(y_test, y_test_proba)

accuracy

0.9788550799381124

In [290]:
make_report(y_test_proba, y_test)

idle test --  316 idle pred --  317
walking test --  561 walking pred --  587
stairs test --  60 stairs_pred --  34
running test --  1002 running pred --  1001


### SVM with scaled gamma

In [291]:
classifier = svm.SVC(decision_function_shape='ovo', probability=True)

scores = cross_val_score(classifier, X_train, y_train, cv=10)
scores.mean()

0.9814291156303113

In [292]:
classifier.fit(X_train, y_train)

y_test_proba = classifier.predict_proba(X_test)

y_test_proba = np.argmax(y_test_proba, axis=1)

accuracy = accuracy_score(y_test, y_test_proba)

accuracy

0.9798865394533265

In [293]:
make_report(y_test_proba, y_test)

idle test --  316 idle pred --  317
walking test --  561 walking pred --  587
stairs test --  60 stairs_pred --  34
running test --  1002 running pred --  1001


### Linear Kernel

In [294]:
classifier = svm.SVC(decision_function_shape='ovo', probability=True, kernel='linear')

scores = cross_val_score(classifier, X_train, y_train, cv=10)
scores.mean()

0.9778907577799918

In [295]:
classifier.fit(X_train, y_train)

y_test_proba = classifier.predict_proba(X_test)

y_test_proba = np.argmax(y_test_proba, axis=1)

accuracy = accuracy_score(y_test, y_test_proba)

accuracy

0.9752449716348633

In [296]:
make_report(y_test_proba, y_test)

idle test --  316 idle pred --  317
walking test --  561 walking pred --  592
stairs test --  60 stairs_pred --  29
running test --  1002 running pred --  1001


# SVM on Stat+FFT Data

In [297]:
from sklearn.model_selection import cross_val_score
from sklearn.metrics import f1_score, accuracy_score
from sklearn import svm

In [298]:
classifier = svm.SVC(decision_function_shape='ovo', kernel='rbf', gamma=0.05, probability=True)

scores = cross_val_score(classifier, X_train, y_train, cv=10)
scores.mean()

0.9750175819023618

In [299]:
classifier.fit(X_train, y_train)

y_test_proba = classifier.predict_proba(X_test)

y_test_proba = np.argmax(y_test_proba, axis=1)

accuracy = accuracy_score(y_test, y_test_proba)

accuracy

0.9783393501805054

In [300]:
make_report(y_test_proba, y_test)

idle test --  316 idle pred --  317
walking test --  561 walking pred --  586
stairs test --  60 stairs_pred --  35
running test --  1002 running pred --  1001


### With Scaled gamma

In [301]:
classifier = svm.SVC(decision_function_shape='ovo', probability=True)

scores = cross_val_score(classifier, X_train, y_train, cv=10)
scores.mean()

0.9814291156303113

In [302]:
classifier.fit(X_train, y_train)

y_test_proba = classifier.predict_proba(X_test)

y_test_proba = np.argmax(y_test_proba, axis=1)

accuracy = accuracy_score(y_test, y_test_proba)

accuracy

0.9793708096957194

In [303]:
make_report(y_test_proba, y_test)

idle test --  316 idle pred --  317
walking test --  561 walking pred --  588
stairs test --  60 stairs_pred --  33
running test --  1002 running pred --  1001


### Linear Kernel

In [304]:
classifier = svm.SVC(decision_function_shape='ovo', probability=True, kernel='linear')

scores = cross_val_score(classifier, X_train, y_train, cv=10)
scores.mean()

0.9778907577799918

In [305]:
classifier.fit(X_train, y_train)

SVC(decision_function_shape='ovo', kernel='linear', probability=True)

In [306]:
y_test_proba = classifier.predict_proba(X_test)

y_test_proba = np.argmax(y_test_proba, axis=1)

accuracy = accuracy_score(y_test, y_test_proba)

accuracy

0.9747292418772563

In [307]:
make_report(y_test_proba, y_test)

idle test --  316 idle pred --  317
walking test --  561 walking pred --  593
stairs test --  60 stairs_pred --  28
running test --  1002 running pred --  1001


In [308]:
classifier.coef_.mean(axis=0)

array([-3.41169647e-01, -6.18732643e-04, -2.56011261e-02,  7.58920521e-03,
       -1.18959493e-01, -3.74407645e-02, -4.40191064e-02, -4.15150532e-02,
        6.94058507e-02, -4.52748631e-04, -8.78383342e-03, -1.53266822e-02,
       -2.41868201e-02, -1.41313184e-03,  1.12678911e-02, -5.93257206e-02,
        3.62757260e-02, -2.26372434e-02,  1.44795364e-02, -5.65959963e-02,
       -1.28980150e-02, -1.48353707e-02,  2.67192881e-02,  5.37972308e-03,
       -5.45519198e-02, -6.75111165e-02,  7.14673266e-04,  5.87734297e-02,
       -9.72618259e-02, -2.20661279e-01, -2.27960465e-02,  1.67056176e-02,
       -4.05331104e-02, -8.56426278e-02, -1.30903664e-01, -4.04789564e-02,
        1.40511573e-01, -7.47463423e-02,  1.46885310e-02, -2.92421587e-02,
       -4.88264990e-03, -1.55893795e-02, -9.78925734e-02, -1.30083193e-02,
        9.39126087e-02, -6.44222944e-02,  5.02946430e-03, -1.30032441e-01,
        7.72418041e-02,  1.59820786e-02,  1.57821652e-01,  3.15201149e-02,
       -4.21055595e-02, -

# Random Forest

In [309]:
from sklearn.model_selection import cross_val_score

In [310]:
from sklearn.ensemble import RandomForestClassifier

clf = RandomForestClassifier(n_estimators=15, max_depth=None)

In [311]:
clf = clf.fit(X_train, y_train)

In [312]:
scores = cross_val_score(clf, X_train, y_train, cv=10)

In [313]:
scores.mean()

0.9801046123190529

In [314]:
y_pred = clf.predict(X_test)

In [315]:
accuracy = accuracy_score(y_test, y_pred)
accuracy

0.9752449716348633

In [316]:
from sklearn.metrics import f1_score

In [317]:
f1score = f1_score(y_test, y_pred, average='macro')
f1score

0.823076923076923

In [318]:
count_idle = 0
count_walking = 0
count_stairs = 0
count_running = 0

for i in y_pred:
  if i==0 :
    count_idle += 1
  elif i==1 :
    count_walking += 1
  elif i==2 :
    count_stairs += 1
  else:
    count_running += 1 

print('idle ', count_idle)
print('walking ', count_walking)
print('stairs ', count_stairs)
print('running ', count_running)

idle  316
walking  609
stairs  12
running  1002


In [319]:
count_idle = 0
count_walking = 0
count_stairs = 0
count_running = 0

for i in y_test:
  if i==0 :
    count_idle += 1
  elif i==1 :
    count_walking += 1
  elif i==2 :
    count_stairs += 1
  else:
    count_running += 1 

print('idle ', count_idle)
print('walking ', count_walking)
print('stairs ', count_stairs)
print('running ', count_running)

idle  316
walking  561
stairs  60
running  1002


# Random Forest Stat Data

In [328]:
from sklearn.model_selection import cross_val_score
from sklearn.metrics import f1_score, accuracy_score
from sklearn.ensemble import RandomForestClassifier

In [329]:
rf_stat = RandomForestClassifier(n_estimators=15, max_depth=None)

In [330]:
scores = cross_val_score(rf_stat, X_train, y_train, cv=10)
scores.mean()

0.9805446482642756

In [331]:
rf_stat = rf_stat.fit(X_train, y_train)

y_pred = rf_stat.predict(X_test)

accuracy = accuracy_score(y_test, y_pred)
accuracy

0.9747292418772563

In [332]:
make_report(y_pred, y_test)

idle test --  316 idle pred --  316
walking test --  561 walking pred --  608
stairs test --  60 stairs_pred --  13
running test --  1002 running pred --  1002


In [333]:
feature_importances = rf_stat.feature_importances_ 

In [334]:
print('Feature importances scaled (*1000)')

for i, f in zip(feature_importances, features):

  print(f, '  ---  ', i*1000)

Feature importances scaled (*1000)
skew_X   ---   77.01703043841424
skew_Y   ---   3.29773239630985
skew_Z   ---   2.565124872415554
kurtosis_X   ---   1.889027793445299
kurtosis_Y   ---   0.861064361592736
kurtosis_Z   ---   3.7489059813731997
max_X   ---   4.158928454392308
max_Y   ---   2.2138184163867396
max_Z   ---   1.1303211127000254
min_X   ---   1.932485098803307
min_Y   ---   1.3565933408081743
min_Z   ---   1.7218460940672229
mean_X   ---   1.7717822070718023
mean_Y   ---   1.4827754729788087
mean_Z   ---   1.0891058482745124
std_X   ---   1.6237714205960752
std_Y   ---   2.0029815674426654
std_Z   ---   1.4793840229995572
variance_X   ---   0.6135121370136267
variance_Y   ---   0.8879039317088454
variance_Z   ---   1.9669463548742656
median_X   ---   2.429096751457832
median_Y   ---   2.52548046609923
median_Z   ---   0.9228976452054133
index_max_X   ---   1.4696025449033476
index_max_Y   ---   1.4981238143861892
index_max_Z   ---   1.144123320242208
index_min_X   ---   1.2

# Random Forest FFT Data

In [335]:
from sklearn.model_selection import cross_val_score
from sklearn.metrics import f1_score, accuracy_score
from sklearn.ensemble import RandomForestClassifier

In [336]:
rf_fft = RandomForestClassifier(n_estimators=50, max_depth=None)

scores = cross_val_score(rf_fft, X_train, y_train, cv=10)
scores.mean()

0.980102658774346

In [337]:
rf_fft = rf_fft.fit(X_train, y_train)

y_pred = rf_fft.predict(X_test)

accuracy = accuracy_score(y_test, y_pred)
accuracy

0.9726663228468283

In [338]:
make_report(y_pred, y_test)

idle test --  316 idle pred --  316
walking test --  561 walking pred --  614
stairs test --  60 stairs_pred --  7
running test --  1002 running pred --  1002


# Random Forest on Stat+FFT Data

In [339]:
from sklearn.model_selection import cross_val_score
from sklearn.metrics import f1_score, accuracy_score
from sklearn.ensemble import RandomForestClassifier

In [340]:
rf = RandomForestClassifier(n_estimators=50, max_depth=None)

scores = cross_val_score(rf, X_train, y_train, cv=10)
scores.mean()

0.9812088534646115

In [341]:
rf = rf.fit(X_train, y_train)

y_pred = rf.predict(X_test)

accuracy = accuracy_score(y_test, y_pred)
accuracy

0.9726663228468283

In [342]:
make_report(y_pred, y_test)

idle test --  316 idle pred --  316
walking test --  561 walking pred --  614
stairs test --  60 stairs_pred --  7
running test --  1002 running pred --  1002


In [343]:
rf.feature_importances_

array([0.1454489 , 0.00311901, 0.00311553, 0.00170565, 0.00202348,
       0.00335122, 0.00298781, 0.0024875 , 0.00164301, 0.00174717,
       0.00185225, 0.00170411, 0.00144076, 0.00156234, 0.00152401,
       0.00263907, 0.00287426, 0.00148588, 0.00208587, 0.00193999,
       0.00143471, 0.00263253, 0.00211822, 0.00135253, 0.00145183,
       0.00159751, 0.0011329 , 0.00138273, 0.0021062 , 0.00373649,
       0.2248771 , 0.00265075, 0.00281699, 0.00117252, 0.00148428,
       0.00164161, 0.00151989, 0.00091567, 0.00118836, 0.00791755,
       0.00728138, 0.00275148, 0.00339801, 0.00240389, 0.0026137 ,
       0.01074096, 0.00599091, 0.01839823, 0.02095895, 0.01445903,
       0.01030445, 0.02427547, 0.02045844, 0.00143748, 0.00135746,
       0.00162369, 0.0012347 , 0.00169802, 0.00175106, 0.00365697,
       0.15157886, 0.0026954 , 0.00204595, 0.00162695, 0.00339759,
       0.00478204, 0.00239346, 0.01277918, 0.0071102 , 0.00550289,
       0.00742116, 0.00337208, 0.0050561 , 0.00351773, 0.00665